In [ ]:
!pip install -U weaviate-client[agents]
!docker-compose up -d
!docker compose exec ollama ollama pull nomic-embed-text
!docker compose exec ollama ollama pull llama3.2

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.7/44.7 kB 2.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.8/44.8 kB 3.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 603.7/603.7 kB 38.4 MB/s eta 0:00:00
/bin/bash: line 1: docker-compose: command not found
/bin/bash: line 1: docker: command not found
/bin/bash: line 1: docker: command not found


In [ ]:
# Below code will go inside a docker compose.yaml file
'''
services:
  weaviate:
    command:
    - --host
    - 0.0.0.0
    - --port
    - '8080'
    - --scheme
    - http
    image: cr.weaviate.io/semitechnologies/weaviate:1.35.1
    ports:
    - 8080:8080
    - 50051:50051
    volumes:
    - weaviate_data:/var/lib/weaviate
    restart: on-failure:0
    environment:
      AUTHENTICATION_ANONYMOUS_ACCESS_ENABLED: 'true'
      PERSISTENCE_DATA_PATH: '/var/lib/weaviate'
      ENABLE_MODULES: 'text2vec-ollama,generative-ollama'
      CLUSTER_HOSTNAME: 'node1'
      OLLAMA_API_ENDPOINT: 'http://ollama:11434'
    depends_on:
      - ollama

  ollama:
    image: ollama/ollama:0.12.9
    ports:
      - "11434:11434"
    volumes:
      - ollama_data:/root/.ollama

volumes:
  weaviate_data:
  ollama_data:

'''

'\nservices:\n  weaviate:\n    command:\n    - --host\n    - 0.0.0.0\n    - --port\n    - \'8080\'\n    - --scheme\n    - http\n    image: cr.weaviate.io/semitechnologies/weaviate:1.35.1\n    ports:\n    - 8080:8080\n    - 50051:50051\n    volumes:\n    - weaviate_data:/var/lib/weaviate\n    restart: on-failure:0\n    environment:\n      AUTHENTICATION_ANONYMOUS_ACCESS_ENABLED: \'true\'\n      PERSISTENCE_DATA_PATH: \'/var/lib/weaviate\'\n      ENABLE_MODULES: \'text2vec-ollama,generative-ollama\'\n      CLUSTER_HOSTNAME: \'node1\'\n      OLLAMA_API_ENDPOINT: \'http://ollama:11434\'\n    depends_on:\n      - ollama\n\n  ollama:\n    image: ollama/ollama:0.12.9\n    ports:\n      - "11434:11434"\n    volumes:\n      - ollama_data:/root/.ollama\n\nvolumes:\n  weaviate_data:\n  ollama_data:\n\n'

In [ ]:
import weaviate
from weaviate.classes.config import Configure

def seed_movies():
    movie_records = [
        {
            "title": "The Matrix",
            "description": (
                "A computer hacker discovers the true nature of reality and "
                "his part in the conflict against its hidden rulers."
            ),
            "genre": "Science Fiction",
        },
        {
            "title": "Spirited Away",
            "description": (
                "A young girl is trapped in a strange spirit realm and must "
                "rescue her parents to return home."
            ),
            "genre": "Animation",
        },
        {
            "title": "The Lord of the Rings: The Fellowship of the Ring",
            "description": (
                "A humble Hobbit and his allies embark on a dangerous quest "
                "to destroy a powerful ring and save Middle-earth."
            ),
            "genre": "Fantasy",
        },
    ]
    return movie_records


# Establish connection to the local Weaviate instance
with weaviate.connect_to_local() as client:
    # Create the Movie collection with Ollama-based vectorization
    client.collections.create(
        name="Movie2",
        vector_config=Configure.Vectors.text2vec_ollama(
            model="nomic-embed-text",
            api_endpoint="http://ollama:11434",  # adjust if running outside Docker
        ),
    )

    movie_collection = client.collections.use("Movie2")
    movies_to_insert = seed_movies()

    # Batch insert objects
    with movie_collection.batch.fixed_size(batch_size=200) as batch:
        for movie in movies_to_insert:
            batch.add_object(properties=movie)

    print(
        f"Imported and vectorized {len(movie_collection)} "
        f"records into the Movie collection"
    )


UnexpectedStatusCodeError: Meta endpoint! Unexpected status code: 404, with response body: None.

In [ ]:
import json
import weaviate


def run_semantic_search(collection, text_query, top_k=2):
    result = collection.query.near_text(
        query=text_query,
        limit=top_k,
    )
    return result.objects


# Open a connection to the local Weaviate instance
with weaviate.connect_to_local() as client:
    movie_collection = client.collections.use("Movie2")

    hits = run_semantic_search(
        collection=movie_collection,
        text_query="sci-fi",
        top_k=2,
    )

    for item in hits:
        print(json.dumps(item.properties, indent=2))
